<div style="text-align: center; font-family: 'charter bt pro roman'; color: #033280;">
  <h1 style="margin-bottom: 10px;">Sentiment Analysis of the Peruvian Fiscal Council's Discipline Using Zero-Shot Learning</h1>
  <div style="height: 2px; width: 90%; margin: 0 auto; background-color: #033280;"></div>
</div>

<div style="text-align: center; font-family: 'charter bt pro roman'; color: #033280;">
  <h2>Documentation</h2>
  <div style="margin-top: 10px;">

<div style="text-align: center; margin-right: 40px;">
  <span style="display: inline-block; margin-right: 10px;">
    <a href="https://github.com/JasonCruz18" target="_blank">
      <img src="https://cdn.jsdelivr.net/gh/devicons/devicon/icons/github/github-original.svg" alt="GitHub" style="width: 24px;">
    </a>
  </span>
  <span style="display: inline-block;">
    <a href="mailto:jj.cruza@up.edu.pe">
      <img src="https://upload.wikimedia.org/wikipedia/commons/4/4e/Mail_%28iOS%29.svg" alt="Email" style="width: 24px;">
    </a>
  </span>
</div>


<div style="font-family: 'PT Serif Pro Book'; text-align: left; color: #1a1a1a; font-size: 16px; line-height: 1.6;">
  This <b style="color: #cd301b;">Jupyter Notebook</b> documents the complete workflow for conducting a <b>sentiment analysis</b> as part of the research project <b>"Advertencias ignoradas: El necesario retorno a la prudencia fiscal en el Perú"</b>.

The notebook is divided into two major sections. The first section focuses on <i>text preprocessing</i> of official <b>announcements</b> and <b>reports</b> from the Peruvian Fiscal Council (Consejo Fiscal, CF), which are publicly available as PDF files on their 
  <a href="https://cf.gob.pe/p/documentos/comunicados/" style="color: #cd301b;">official website</a>. This section includes the extraction of raw data and metadata, the segmentation of documents into paragraphs, and the removal of textual noise — all crucial steps to prepare the data for sentiment classification.

The second section applies a <b>zero-shot learning approach</b> using the <code>xlm-roberta-base</code> model from Hugging Face's Transformers library. This allows us to evaluate the sentiment of each paragraph based on custom-defined fiscal labels, without requiring any fine-tuning on labeled training data. The process includes defining the set of sentiment labels, feeding the model with each paragraph, and aggregating the results by document or publication to assess the overall tone of fiscal communication.

The goal is to provide a rigorous and reproducible methodology for analyzing the <b>disciplinary tone</b> expressed by the Fiscal Council — an independent institution — in its published content, contributing to the broader understanding of Peru’s fiscal credibility and oversight.
</div>


<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;line-height: 1.5;">
<span style="font-size: 24px;">&#128196;</span> This icon refers <i>Announcement</i> or <i>Report</i> (<i>A/R</i>) of the CF.
    <br>
    <span style="font-size: 24px;">&#8987;</span> A/R available since <b>2016-</b>. 
    <br>
</div>

<div style="font-family: Amaya; text-align: left; color: #033280; font-size:16px">The following <b>outline is functional</b>. By utilising the provided buttons, users are able to enhance their experience by browsing this script.<div/>

<div id="outilne"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #E0E0E0;">
        Outline
    </h2>
    <br>
    <a href="#libraries" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        Libraries</a>
    <br>
    <a href="#setup" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        Initial set-up</a>
    <br>
    <a href="#1" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        1. Preprocessing text</a>
    <br>
    <a href="#1-1" style="color: #ff8575; font-size: 16px; margin-left: 20px;">
        1.1 Raw data</a>
    <br>
    <a href="#1-2" style="color: #ff8575; font-size: 16px; margin-left: 20px;">
        1.2 Metadata</a>
    <br>
    <a href="#1-3" style="color: #ff8575; font-size: 16px; margin-left: 20px;">
        1.3 Split into paragraphs</a>
    <br>
    <a href="#1-4" style="color: #ff8575; font-size: 16px; margin-left: 20px;">
        1.4 Noise reduction</a>
    <br>
    <a href="#2" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        2. Sentiment analysis by zero-shot</a>
     <br>
    <a href="#2-1" style="color: #ff8575; font-size: 16px; margin-left: 20px;">
        2.1 Define the model (<code>xlm-roberta-base</code>)</a>
    <br>
    <a href="#2-2" style="color: #ff8575; font-size: 16px; margin-left: 20px;">
        2.2 Define the labels</a>
    <br>
    <a href="#2-3" style="color: #ff8575; font-size: 16px; margin-left: 20px;">
        2.3 Applying the model to the paragraphs</a>
    <br>
    <a href="#2-4" style="color: #ff8575; font-size: 16px; margin-left: 20px;">
        2.4 Sentiment aggregation by announcement</a>
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    Any questions or issues regarding the coding, please email Jason Cruz <a href="mailto:jj.cruza@alum.up.edu.pe" style="color: rgb(0, 153, 123); text-decoration: none;"><span style="font-size: 24px;">&#x2709;</span>
    </a>.
    <div/>

<div id="libraries"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h1 style="text-align: left; color: #E0E0E0;">
        Libraries
    </h1>
</div>

In [1]:
from openai import OpenAI
import numpy as np
import pandas as pd
from py_markdown_table.markdown_table import markdown_table

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">Back to the outline.</a>
</div>

<div id="setup"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h1 style="text-align: left; color: #E0E0E0;">
        Initial set-up
    </h1>
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    Check your Python version.
    <div/>

In [2]:
!python --version

Python 3.12.11


<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    If you don't have the libraries below, please use the following code (as example) to install the required libraries. The following code lines will install all the dependences
    <div/>

In [ ]:
!pip install numpy pandas openai tiktoken py_markdown_table pdfplumber --quiet && !pip install pymupdf nltk pandas --quiet > nul 2>&1

In [ ]:
!pip install matplotlib --quiet > nul 2>&1

In [ ]:
!pip install seaborn --quiet > nul 2>&1

In [ ]:
!pip install pytesseract pdf2image pillow --quiet > nul 2>&1

In [ ]:
!pip install langid

<div style="font-family: PT Serif Pro Book; text-align: left; color:dark; font-size:16px"> The following code lines will allow us to display the entire dataframes. <div/>

In [3]:
# Evitar que pandas trunque el texto al mostrarlo
pd.set_option('display.max_colwidth', None)

In [4]:
# Evitar que pandas trunque el texto al mostrarlo
pd.set_option('display.max_row', None)

<p style="font-family: PT Serif Pro Book; text-align: left; color:dark; font-size:16px"> The following function will establish a connection to the <code>cf_mef_datasets</code> database in <code>PostgreSQL</code>. The <b>input data</b> used in this jupyter notebook will be loaded from this <code>PostgreSQL</code> database, and similarly, all <b>output data</b> generated by this jupyter notebook will be stored in that database. Ensure that you set the necessary parameters to access the server once you have obtained the required permissions.<p/>
    
<p style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
To request permissions, please email Jason Cruz <a href="mailto:jj.cruza@alum.up.edu.pe" style="color: #cd301b; text-decoration: none;"> <span style="font-size: 24px;">&#x2709;</span>
    </a>.
<p/>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    <span style="font-size: 24px; color: #FFA823; font-weight: bold;">&#9888;</span>
    Enter your user credentials to acces to SQL.
    <div/>

In [ ]:
def create_sqlalchemy_engine():
    """
    Function to create an SQLAlchemy engine using environment variables.
    
    Returns:
        engine: SQLAlchemy engine object.
    """
    # Get environment variables
    user = os.environ.get('CIUP_SQL_USER')  # Get the SQL user from environment variables
    password = os.environ.get('CIUP_SQL_PASS')  # Get the SQL password from environment variables
    host = os.environ.get('CIUP_SQL_HOST')  # Get the SQL host from environment variables
    port = 5432  # Set the SQL port to 5432
    database = 'gdp_revisions_datasets'  # Set the database name 'gdp_revisions_datasets' from SQL

    # Check if all environment variables are defined
    if not all([host, user, password]):
        raise ValueError("Some environment variables are missing (CIUP_SQL_HOST, CIUP_SQL_USER, CIUP_SQL_PASS)")

    # Create connection string
    connection_string = f"postgresql://{user}:{password}@{host}:{port}/{database}"

    # Create SQLAlchemy engine
    engine = create_engine(connection_string)
    
    return engine

<div style="text-align: left;">
    <span style="font-size: 24px; color: rgb(255, 32, 78); font-weight: bold;">&#9888;</span>
    <span style="font-family: PT Serif Pro Book; color: black; font-size: 16px;">
        Import all other functions required by this jupyter notebook.
    </span>
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color:dark; font-size:16px"> Please, check the script <code>cf_mef_functions.py</code> which contains all the functions required by this jupyter notebook. The functions there are ordered according to the <a href="#outilne" style="color: #033280;">sections</a> of this jupyter notebok.<div/>

In [ ]:
#from cf_mef_functions.py import * 

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

<div id="1"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h1 style="text-align: left; color: #E0E0E0;">
        1. Preprocessing text
    </h1>
</div>

In [5]:
import re
import pandas as pd
import pdfplumber
import os
import fitz  # PyMuPDF
from datetime import datetime

In [6]:
import os
import pandas as pd
from pdf2image import convert_from_path
import pytesseract
from PIL import Image

In [7]:
import os
from pdf2image import convert_from_path
import pytesseract

In [8]:
import unicodedata

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

<div id="1-1"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #ff8575;">
        1.1 Raw data
    </h2>
</div>

<div id="1-2"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #ff8575;">
        1.2 Metadata
    </h2>
</div>

This function processes all PDF files in a specified folder to extract their raw text
and add metadata such as 'announcement', 'year', and 'date'. The extracted data is 
returned as a DataFrame.

Parameters:
folder_path (str): The folder path where the PDF files are located.

Returns:
pd.DataFrame: A DataFrame with columns: 'filename', 'year', 'date', 'announcement', 'raw_text'

* Doucumentar Tesseract instalar y llamar desde la path donde está .exe

# CF comunicados

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

# CF informes

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

Extracts raw text from scanned PDFs using OCR.

Args:
    folder_path (str): Path to the folder containing PDF files.
    dpi (int): Resolution of the images extracted from the PDF.
    lang (str): Language for OCR ('spa' for Spanish, 'eng' for English, etc.)

Returns:
    pd.DataFrame: DataFrame with columns ['filename', 'raw_text']

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

<div id="1-3"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #ff8575;">
        1.3 Split into paragraphs
    </h2>
</div>

# EDITABLE

### Procesa PDFs editables extrayendo metadatos y párrafos por página.

    Args:
        folder_path (str): Ruta a la carpeta con los archivos PDF.

    Returns:
        pd.DataFrame: DataFrame con columnas
            ['filename', 'year', 'date', 'announcement', 'page', 'paragraph_id', 'text']

    """
    Procesa PDFs editables extrayendo párrafos por página y metadatos del mismo texto ya procesado.

    Args:
        folder_path (str): Ruta a la carpeta con los archivos PDF.

    Returns:
        pd.DataFrame: DataFrame con columnas:
            ['filename', 'year', 'date', 'announcement', 'page', 'paragraph_id', 'text']
    """

In [10]:
import os
import re
import pdfplumber
import pandas as pd

def process_editable_pdfs(folder_path):
    all_records = []
    date_pattern = re.compile(
        r"Lima[,]?\s+(\d{1,2})\s+de\s+([a-záéíóú]+)\s+de\s+(\d{4})",
        flags=re.IGNORECASE
    )

    for filename in os.listdir(folder_path):
        if not filename.lower().endswith(".pdf"):
            continue

        file_path = os.path.join(folder_path, filename)

        try:
            print(f"Procesando: {filename}")
            with pdfplumber.open(file_path) as pdf:
                full_text_parts = []
                paragraph_counter = 1

                for page_num, page in enumerate(pdf.pages, start=1):
                    # ---- 1. Extraer palabras con atributos visuales ----
                    words = page.extract_words(extra_attrs=["size", "top"])
                    FONT_MIN = 11.0
                    FONT_MAX = 11.9

                    # ---- 2. Filtrar por tamaño de fuente ----
                    clean_words = [
                        w for w in words
                        if FONT_MIN <= w["size"] <= FONT_MAX
                    ]

                    if not clean_words:
                        continue

                    # ---- 3. Reconstruir líneas por posición vertical (top) ----
                    lines_dict = {}
                    for word in clean_words:
                        line_top = round(word["top"], 1)
                        lines_dict.setdefault(line_top, []).append(word["text"])

                    lines = [
                        " ".join(words).strip()
                        for _, words in sorted(lines_dict.items())
                        if words
                    ]

                    if not lines:
                        continue

                    page_text = "\n".join(lines)
                    full_text_parts.append(page_text)

                    # ---- 4. Detectar párrafos ----
                    lines = page_text.strip().split("\n")
                    lines = [line.strip() for line in lines if line.strip()]
                    paragraph_lines = []

                    for i, line in enumerate(lines):
                        is_new_paragraph = (
                            line.startswith("•")
                            or line.startswith("➢")
                            or (i > 0 and lines[i - 1].strip().endswith("."))
                            or (i > 0 and len(lines[i - 1].split()) <= 3)
                        )

                        if is_new_paragraph:
                            if paragraph_lines:
                                current_paragraph = " ".join(paragraph_lines).strip()
                                all_records.append({
                                    "filename": filename,
                                    "page": page_num,
                                    "paragraph_id": paragraph_counter,
                                    "text": current_paragraph
                                })
                                paragraph_counter += 1
                            paragraph_lines = [line]
                        else:
                            paragraph_lines.append(line)

                    if paragraph_lines:
                        final_paragraph = " ".join(paragraph_lines).strip()
                        all_records.append({
                            "filename": filename,
                            "page": page_num,
                            "paragraph_id": paragraph_counter,
                            "text": final_paragraph
                        })
                        paragraph_counter += 1

                # ---- 5. Extraer metadatos ----
                full_text = "\n".join(full_text_parts)

                announcement = None
                year = None
                date = None

                match = re.search(r'Comunicado\s+N[°º]?\s*(\d{2})-(\d{4})-CF', full_text, re.IGNORECASE)
                if not match:
                    match = re.search(r'(\d{2})-(\d{4})', filename)
                if match:
                    announcement = match.group(1)
                    year = match.group(2)

                date_match = date_pattern.search(full_text)
                if date_match:
                    day, month, year_from_date = date_match.groups()
                    date = f"{int(day)} de {month.lower()} de {year_from_date}"
                    if not year:
                        year = year_from_date

                for record in all_records:
                    if record["filename"] == filename:
                        record["year"] = year
                        record["date"] = date
                        record["announcement"] = announcement

        except Exception as e:
            print(f"Error procesando {filename}: {e}")

    df = pd.DataFrame(all_records)
    df = df[["filename", "year", "date", "announcement", "page", "paragraph_id", "text"]]
    return df



In [11]:
df_parrafos = process_editable_pdfs(r"C:\Users\Jason Cruz\OneDrive\Documentos\RA\CIUP\Policy Brief\CF\opiniones")

Procesando: CF-Informe-IAPM21-vF.pdf
Procesando: CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf
Procesando: CF-Informe-MMM2124-publicado-enviado-CF-VF.pdf
Procesando: CF-Pronunciamiento-DU-032-2019-VERSIÓN-FINAL.pdf
Procesando: CF-Pronunciamiento-MMM-2019-2022_15_8_2018-enviada-al-MEF-1.pdf
Procesando: CF-Pronunciamiento-MMM-2020-2023-Versión-Final-9pm.pdf
Procesando: CF-Pronunciamiento.pdf
Procesando: Informe-DL1621-vf.pdf
Procesando: Informe-Escenarios-_8.6.2020_FINAL.pdf
Procesando: Informe-GobSubnacionales-2021-vF.pdf
Procesando: Informe-N°-005-2020-CF.pdf
Procesando: Informe-PLReglasFiscales-2022.pdf
Procesando: Informe-ReglasGRsLs-VF-publicado.pdf
Procesando: Informe01-OpinionCFIAPM2023.pdf
Procesando: InformeCF-IAPM-VF.pdf
Procesando: Opinion-MMM2023-2026-cNotaAclaratoria.pdf
Procesando: Pronunciamiento-CF-DCRF-2017-12julio-enviada-1.pdf
Procesando: Pronunciamiento-CF-DCRF-2018-VF-publicada.pdf
Procesando: Pronunciamiento-COVID-CF-VF.pdf
Procesando: Pronunciam

In [12]:
df_parrafos

filename  year  \
0                                              CF-Informe-IAPM21-vF.pdf  2021   
1                                              CF-Informe-IAPM21-vF.pdf  2021   
2                                              CF-Informe-IAPM21-vF.pdf  2021   
3                                              CF-Informe-IAPM21-vF.pdf  2021   
4                                              CF-Informe-IAPM21-vF.pdf  2021   
5                                              CF-Informe-IAPM21-vF.pdf  2021   
6                                              CF-Informe-IAPM21-vF.pdf  2021   
7                                              CF-Informe-IAPM21-vF.pdf  2021   
8                                              CF-Informe-IAPM21-vF.pdf  2021   
9                                              CF-Informe-IAPM21-vF.pdf  2021   
10                                             CF-Informe-IAPM21-vF.pdf  2021   
11                                             CF-Informe-IAPM21-vF.pdf  2021   
12                                             CF-Informe-IAPM21-vF.pdf  2021   
13                                             CF-Informe-IAPM21-vF.pdf  2021   
14                                             CF-Informe-IAPM21-vF.pdf  2021   
15                                             CF-Informe-IAPM21-vF.pdf  2021   
16                                             CF-Informe-IAPM21-vF.pdf  2021   
17                                             CF-Informe-IAPM21-vF.pdf  2021   
18                                             CF-Informe-IAPM21-vF.pdf  2021   
19                                             CF-Informe-IAPM21-vF.pdf  2021   
20                                             CF-Informe-IAPM21-vF.pdf  2021   
21                                             CF-Informe-IAPM21-vF.pdf  2021   
22                                             CF-Informe-IAPM21-vF.pdf  2021   
23                                             CF-Informe-IAPM21-vF.pdf  2021   
24                                             CF-Informe-IAPM21-vF.pdf  2021   
25                                             CF-Informe-IAPM21-vF.pdf  2021   
26                                             CF-Informe-IAPM21-vF.pdf  2021   
27                                             CF-Informe-IAPM21-vF.pdf  2021   
28                                             CF-Informe-IAPM21-vF.pdf  2021   
29                                             CF-Informe-IAPM21-vF.pdf  2021   
30                                             CF-Informe-IAPM21-vF.pdf  2021   
31                                             CF-Informe-IAPM21-vF.pdf  2021   
32                                             CF-Informe-IAPM21-vF.pdf  2021   
33                                             CF-Informe-IAPM21-vF.pdf  2021   
34                                             CF-Informe-IAPM21-vF.pdf  2021   
35                                             CF-Informe-IAPM21-vF.pdf  2021   
36                                             CF-Informe-IAPM21-vF.pdf  2021   
37                                             CF-Informe-IAPM21-vF.pdf  2021   
38                                             CF-Informe-IAPM21-vF.pdf  2021   
39                                             CF-Informe-IAPM21-vF.pdf  2021   
40                                             CF-Informe-IAPM21-vF.pdf  2021   
41                                             CF-Informe-IAPM21-vF.pdf  2021   
42                                             CF-Informe-IAPM21-vF.pdf  2021   
43                                             CF-Informe-IAPM21-vF.pdf  2021   
44                                             CF-Informe-IAPM21-vF.pdf  2021   
45                                             CF-Informe-IAPM21-vF.pdf  2021   
46                                             CF-Informe-IAPM21-vF.pdf  2021   
47                                             CF-Informe-IAPM21-vF.pdf  2021   
48    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
49    CF-Info

In [16]:
def clean_noise(df):
    df_clean = df.copy()
    rows = []

    for _, row in df_clean.iterrows():
        text = row["text"].strip()
        
    
        # Paso 0: Normalizar texto Unicode
        text = unicodedata.normalize("NFKC", text)
        
        # 
        text = re.sub(r"\b\d+/\d+\b", "", text)
        
        # Paso 1: Eliminar espacios múltiples y extremos
        text = re.sub(r"\s+([,;:.!?])", r"\1", text)
        
        # Paso 2: Remover URL
        text = re.sub(r"https?://|www\.\w+\.\w+", "", text)
        
        # Paso 3: Eliminar símbolos no deseados
        text = re.sub(r"[•➢Ø*°¡!?¿\"]", "", text)
        
        # Paso 4: Reemplazar ":" final por "."
        if text.endswith(":"):
            text = text[:-1].rstrip() + "."
            
        # Paso 5: Remover expresiones tipo "Lima, 24 de noviembre de 2020" o "Lima 16 de diciembre de 2020"
        text = re.sub(
            r"Lima[,]?\s+\d{1,2}\s+de\s+[a-záéíóú]+\s+de\s+\d{4}",
            "",
            text,
            flags=re.IGNORECASE
        )
        
        # Paso 9: Eliminar si empieza con "Fuente:"
        if text.lower().startswith("fuente:"):
            continue
        
        # Paso 10: Eliminar si contiene "Fuente:" o "Elaboración:" exactamente
        if re.search(r"\b(Fuente:|Elaboración:)", text, flags=re.IGNORECASE):
            continue
                    
        # Reconstruir DataFrame con observaciones válidas
        df_result = pd.DataFrame(rows).reset_index(drop=True)

        # Paso 11: Fusionar observaciones consecutivas
        i = 0
        while i < len(df_result) - 1:
            curr_text = df_result.at[i, "text"].strip()
            next_text = df_result.at[i + 1, "text"].strip()

            # Condición 1: curr no termina en punto, next empieza con letra y termina en punto
            if not curr_text.endswith(".") and next_text and next_text[0].isalpha() and next_text.endswith("."):
                df_result.at[i, "text"] = curr_text + " " + next_text
                df_result = df_result.drop(i + 1).reset_index(drop=True)
                continue

            # Condición 2: curr sin punto final, next empieza con un año
            if not curr_text.endswith(".") and re.match(r"^\d{4}", next_text):
                df_result.at[i, "text"] = curr_text + " " + next_text
                df_result = df_result.drop(i + 1).reset_index(drop=True)
                continue

            i += 1
        
        # Paso 12: Eliminar si tiene menos de 6 palabras
        if len(text.split()) < 6:
            continue
        
        # Paso 13: Eliminar si mayoría de caracteres son mayúsculas
        letters = [c for c in text if c.isalpha()]
        if letters:
            upper_ratio = sum(c.isupper() for c in letters) / len(letters)
            if upper_ratio > 0.7:
                continue
            
        # Paso 14: Reemplazar "p.p." por "puntos porcentuales"
        text = text.replace("p.p.", "puntos porcentuales")
            
        # Paso 15: Eliminar si contiene letras intercaladas por espacios (3+ letras)
        if re.search(r"(?:\b\w\s){3,}\w", text):
            continue
            
        # Paso 16: Eliminar si contiene fecha tipo "Lima, 20 de abril de 2023"
        if re.search(r"Lima[,]?\s+\d{1,2}\s+de\s+[a-záéíóú]+\s+de\s+\d{4}", text, re.IGNORECASE):
            continue
            
        # Paso 17: Eliminar si contiene el siguiente patrón
        if re.search(r'PCA\s*(Inicial|1er\s*Trim\.|2do\s*Trim\.|3er\s*Trim\.)', text, flags=re.IGNORECASE):
            continue
        
        # Paso 18: Eliminar si contiene patrón sobre leyes por insistencia
        if re.search(r'entre\s+\d{4}\sy\s+\d{4}\s*,?\s*\d+\s*de\s+cada\s+100\s*(leyes?|insistencia|implicancia\s*fiscal)', text, flags=re.IGNORECASE):
            continue
        
        # Paso 19: Eliminar si contiene comillas con referencias tipo (pág. x)
        if re.search(r'“[^”]*\(pág\.\s*\d+\)[^”]*”|\(pág\.\s*\d+\)', text, flags=re.IGNORECASE):
            continue
            
        # Paso 20: Eliminar punto final si palabra anterior es preposición o conector
        if re.search(r"\b(?:a|al|de|del|con|por|para|y|o|en|sin|sobre|ante|tras|entre|hacia|hasta|durante|mediante|excepto|salvo|según)\.$", text):
            text = text[:-1]
            
        # Paso 21: Eliminar ítems al inicio del texto (solo al inicio)
        text = re.sub(
            r'^\s*((?:[ivxlcdm]+|[a-zA-Z]|\d+)[\.\)]\s*)+', 
            '', 
            text, 
            flags=re.IGNORECASE
        ).strip()
        
        # Paso 22
        
        if re.search(r"\banexo\s*\d+\b", text, flags=re.IGNORECASE):
            text = ""
            
            
        # Paso
        # Paso X: Eliminar si contiene referencia a múltiples informes del CF
        if re.search(r"Véase informes\s+(N°\s*\d{2}-\d{4}-CF[, y]*){2,}", text, flags=re.IGNORECASE):
            continue
            
        # Paso 25.6: Eliminar si contiene referencias documentales como "Véase el artículo", "Ver Informe", etc.
        if re.search(r"\b(Véase|Ver|Consultar|Remítase|Revísese)\s+(el\s+)?(informe|artículo|documento|reporte|análisis|dictamen)", text, flags=re.IGNORECASE):
            continue
            
            
        # Paso 25.7: Eliminar si contiene el símbolo "¢" o "¢US"
        if re.search(r"¢\s*US?|US?\s*¢", text, flags=re.IGNORECASE) or "¢" in text:
            continue    
            
        # Paso 25.8: Eliminar si contiene expresiones tipo (MMM: -3,5%) o (MMM: -3,5 %)
        if re.search(r"\(MMM:\s*-?\d+,\d+\s*%\)", text):
            continue
            
        # Reconstruir DataFrame con observaciones válidas
        df_result = pd.DataFrame(rows).reset_index(drop=True)    

        # Paso XX: Guardar fila limpia
        new_row = row.copy()
        new_row["text"] = text
        rows.append(new_row)
        
        # Paso 11: Fusionar observaciones consecutivas
        i = 0
        while i < len(df_result) - 1:
            curr_text = df_result.at[i, "text"].strip()
            next_text = df_result.at[i + 1, "text"].strip()

            # Condición 1: curr no termina en punto, next empieza con letra y termina en punto
            if not curr_text.endswith(".") and next_text and next_text[0].isalpha() and next_text.endswith("."):
                df_result.at[i, "text"] = curr_text + " " + next_text
                df_result = df_result.drop(i + 1).reset_index(drop=True)
                continue

            # Condición 2: curr sin punto final, next empieza con un año
            if not curr_text.endswith(".") and re.match(r"^\d{4}", next_text):
                df_result.at[i, "text"] = curr_text + " " + next_text
                df_result = df_result.drop(i + 1).reset_index(drop=True)
                continue

            i += 1

    


    # Recalcular paragraph_id por documento
    df_result["paragraph_id"] = df_result.groupby("filename").cumcount() + 1
    

    
    return df_result





In [17]:
df_parrafos_cleaned = clean_noise(df_parrafos)

In [19]:
df_parrafos_cleaned

filename  year  \
0                                              CF-Informe-IAPM21-vF.pdf  2021   
1                                              CF-Informe-IAPM21-vF.pdf  2021   
2                                              CF-Informe-IAPM21-vF.pdf  2021   
3                                              CF-Informe-IAPM21-vF.pdf  2021   
4                                              CF-Informe-IAPM21-vF.pdf  2021   
5                                              CF-Informe-IAPM21-vF.pdf  2021   
6                                              CF-Informe-IAPM21-vF.pdf  2021   
7                                              CF-Informe-IAPM21-vF.pdf  2021   
8                                              CF-Informe-IAPM21-vF.pdf  2021   
9                                              CF-Informe-IAPM21-vF.pdf  2021   
10                                             CF-Informe-IAPM21-vF.pdf  2021   
11                                             CF-Informe-IAPM21-vF.pdf  2021   
12                                             CF-Informe-IAPM21-vF.pdf  2021   
13                                             CF-Informe-IAPM21-vF.pdf  2021   
14                                             CF-Informe-IAPM21-vF.pdf  2021   
15                                             CF-Informe-IAPM21-vF.pdf  2021   
16                                             CF-Informe-IAPM21-vF.pdf  2021   
17                                             CF-Informe-IAPM21-vF.pdf  2021   
18                                             CF-Informe-IAPM21-vF.pdf  2021   
19                                             CF-Informe-IAPM21-vF.pdf  2021   
20                                             CF-Informe-IAPM21-vF.pdf  2021   
21                                             CF-Informe-IAPM21-vF.pdf  2021   
22                                             CF-Informe-IAPM21-vF.pdf  2021   
23                                             CF-Informe-IAPM21-vF.pdf  2021   
24                                             CF-Informe-IAPM21-vF.pdf  2021   
25                                             CF-Informe-IAPM21-vF.pdf  2021   
26                                             CF-Informe-IAPM21-vF.pdf  2021   
27                                             CF-Informe-IAPM21-vF.pdf  2021   
28                                             CF-Informe-IAPM21-vF.pdf  2021   
29                                             CF-Informe-IAPM21-vF.pdf  2021   
30                                             CF-Informe-IAPM21-vF.pdf  2021   
31                                             CF-Informe-IAPM21-vF.pdf  2021   
32                                             CF-Informe-IAPM21-vF.pdf  2021   
33                                             CF-Informe-IAPM21-vF.pdf  2021   
34                                             CF-Informe-IAPM21-vF.pdf  2021   
35                                             CF-Informe-IAPM21-vF.pdf  2021   
36                                             CF-Informe-IAPM21-vF.pdf  2021   
37                                             CF-Informe-IAPM21-vF.pdf  2021   
38                                             CF-Informe-IAPM21-vF.pdf  2021   
39                                             CF-Informe-IAPM21-vF.pdf  2021   
40    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
41    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
42    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
43    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
44    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
45    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
46    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
47    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
48    CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
49    CF-Info

"""
Procesa PDFs escaneados usando OCR para extraer párrafos por página y metadatos.

Args:
    folder_path (str): Ruta a la carpeta con archivos PDF escaneados.
    dpi (int): Resolución al convertir PDF a imagen.
    lang (str): Idioma para el OCR ('spa' para español, 'eng' para inglés, etc.).

Returns:
    pd.DataFrame: DataFrame con columnas:
        ['filename', 'year', 'date', 'announcement', 'page', 'paragraph_id', 'text']
"""    

In [ ]:
import os
import re
import pandas as pd
from pdf2image import convert_from_path
import pytesseract

# Configurar Tesseract (ajusta si está en otra ruta)
pytesseract.pytesseract.tesseract_cmd = r"C:\Program Files\Tesseract-OCR\tesseract.exe"

def process_scanned_pdfs(folder_path, dpi=300, lang='spa'):

    all_records = []
    date_pattern = re.compile(
        r"Lima[,]?\s+(\d{1,2})\s+de\s+([a-záéíóú]+)\s+de\s+(\d{4})",
        flags=re.IGNORECASE
    )

    for filename in os.listdir(folder_path):
        if not filename.lower().endswith(".pdf"):
            continue

        file_path = os.path.join(folder_path, filename)

        try:
            print(f"Procesando: {filename}")
            images = convert_from_path(file_path, dpi=dpi)
            full_text_parts = []
            paragraph_counter = 1

            for page_num, img in enumerate(images, start=1):
                page_text = pytesseract.image_to_string(img, lang=lang)
                if not page_text.strip():
                    continue

                full_text_parts.append(page_text)

                lines = page_text.strip().split("\n")
                lines = [line.strip() for line in lines if line.strip()]
                paragraph_lines = []

                for i, line in enumerate(lines):
                    is_new_paragraph = (
                        line.startswith("•")
                        or line.startswith("➢")
                        or (i > 0 and lines[i - 1].strip().endswith("."))
                        or (i > 0 and len(lines[i - 1].split()) <= 3)
                    )

                    if is_new_paragraph:
                        if paragraph_lines:
                            current_paragraph = " ".join(paragraph_lines).strip()
                            all_records.append({
                                "filename": filename,
                                "page": page_num,
                                "paragraph_id": paragraph_counter,
                                "text": current_paragraph
                            })
                            paragraph_counter += 1
                        paragraph_lines = [line]
                    else:
                        paragraph_lines.append(line)

                if paragraph_lines:
                    final_paragraph = " ".join(paragraph_lines).strip()
                    all_records.append({
                        "filename": filename,
                        "page": page_num,
                        "paragraph_id": paragraph_counter,
                        "text": final_paragraph
                    })
                    paragraph_counter += 1

            # Extraer metadatos desde el texto acumulado por OCR
            full_text = "\n".join(full_text_parts)

            announcement = None
            year = None
            date = None

            match = re.search(r'Comunicado\s+N[°º]?\s*(\d{2})-(\d{4})-CF', full_text, re.IGNORECASE)
            if not match:
                match = re.search(r'(\d{2})-(\d{4})', filename)
            if match:
                announcement = match.group(1)
                year = match.group(2)

            date_match = date_pattern.search(full_text)
            if date_match:
                day, month, year_from_date = date_match.groups()
                date = f"{int(day)} de {month.lower()} de {year_from_date}"
                if not year:
                    year = year_from_date

            # Asignar metadatos a cada párrafo
            for record in all_records:
                if record["filename"] == filename:
                    record["year"] = year
                    record["date"] = date
                    record["announcement"] = announcement

        except Exception as e:
            print(f"Error procesando {filename}: {e}")

    # Convertir a DataFrame y ordenar columnas
    df = pd.DataFrame(all_records)
    df = df[["filename", "year", "date", "announcement", "page", "paragraph_id", "text"]]
    return df


In [ ]:
df_scanned = process_scanned_pdfs(r"C:\Users\Jason Cruz\OneDrive\Documentos\RA\CIUP\Policy Brief\CF\opiniones\scanned")

In [ ]:
df_scanned

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

<div id="1-4"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #ff8575;">
        1.4 Noise reduction
    </h2>
</div>

In [ ]:
import regex

In [ ]:
def clean_noise(df):
    df_clean = df.copy()
    rows = []

    for _, row in df_clean.iterrows():
        text = row["text"].strip()
        
    
        # Paso 0: Normalizar texto Unicode
        text = unicodedata.normalize("NFKC", text)
        
        
            
            

        # Paso 26: Guardar fila limpia
        new_row = row.copy()
        new_row["text"] = text
        rows.append(new_row)

    # Reconstruir DataFrame con observaciones válidas
    df_result = pd.DataFrame(rows).reset_index(drop=True)

    # Paso 27: Fusionar observaciones consecutivas
    i = 0
    while i < len(df_result) - 1:
        curr_text = df_result.at[i, "text"].strip()
        next_text = df_result.at[i + 1, "text"].strip()

        # Condición 1: curr no termina en punto, next empieza con letra y termina en punto
        if not curr_text.endswith(".") and next_text and next_text[0].isalpha() and next_text.endswith("."):
            df_result.at[i, "text"] = curr_text + " " + next_text
            df_result = df_result.drop(i + 1).reset_index(drop=True)
            continue

        # Condición 2: curr sin punto final, next empieza con un año
        if not curr_text.endswith(".") and re.match(r"^\d{4}", next_text):
            df_result.at[i, "text"] = curr_text + " " + next_text
            df_result = df_result.drop(i + 1).reset_index(drop=True)
            continue

        i += 1
        
        
    # Paso 28: Eliminar página 7 del Comunicado 05-2024 del 20 de diciembre de 2024 (es un anexo)
    df_result = df_result[
        ~(
            (df_result["page"] == 7)
            & (df_result["year"] == "2024")
            & (df_result["announcement"] == "05")
            & (df_result["date"] == "20 de diciembre de 2024")
        )
    ].reset_index(drop=True)
    
    # Paso 29: Eliminar página 7 del Comunicado 05-2024 del 20 de diciembre de 2024 (es un anexo)
    df_result = df_result[
        ~(
            (df_result["page"] >= 8)
            & (df_result["year"] == "2017")
            & (df_result["announcement"] == "03")
            & (df_result["date"] == "21 de junio de 2017")
        )
    ].reset_index(drop=True)

    # Recalcular paragraph_id por documento
    df_result["paragraph_id"] = df_result.groupby("filename").cumcount() + 1
    

    
    return df_result



In [ ]:
    # Paso 23: Conservar solo observaciones con keywords clave de advertencia fiscal
    keywords = [
        "Incumplimiento de reglas fiscales", "Preocupación", "Advertencia", "Alerta",
        "Riesgos fiscales", "Desvío del déficit fiscal", "No cumplimiento", "Desviaciones significativas",
        "Margen significativo", "Problema de credibilidad fiscal", "Credibilidad fiscal",
        "Sostenibilidad fiscal", "Consolidación fiscal", "Medidas correctivas", "Recomendación",
        "Necesidad de tomar medidas", "Control del gasto público", "Presiones fiscales",
        "Exceso de optimismo en proyecciones", "Exceso de gasto", "Aumento de gasto",
        "Reducción de déficit fiscal", "Incremento de ingresos permanentes",
        "Falta de compromiso con la responsabilidad fiscal", "Medidas de consolidación",
        "Deficiencia en la ejecución del gasto", "Aumento de la deuda pública",
        "Iniciativas legislativas que afectan las finanzas públicas", "Incremento del gasto público",
        "Beneficios tributarios sin justificación", "Tratamientos tributarios preferenciales",
        "Erosión de la base tributaria", "Elusión y evasión tributaria",
        "Aumento de gastos no previstos", "Aumento de gastos extraordinarios",
        "Aumento de gastos en remuneraciones", "Crecimiento del gasto no financiero",
        "Problema de sostenibilidad", "Riesgos de sostenibilidad fiscal", "Aumento de deuda neta",
        "Desajuste fiscal", "Falta de transparencia en el gasto", "Riesgos de sobreendeudamiento",
        "Excepciones a las reglas fiscales", "Riesgo de incumplimiento de metas fiscales",
        "Aumento de los compromisos de deuda", "Riesgo de insolvencia",
        "Falta de flexibilidad fiscal", "Desajuste entre el presupuesto y el MMM",
        "Riesgo de incumplimiento debido a presiones de gasto", "Erosión de la capacidad recaudatoria",
        "Incremento de la deuda pública", "Falta de control de gastos extraordinarios",
        "Necesidad de ajustar el gasto", "Inestabilidad macroeconómica",
        "Problemas fiscales derivados de iniciativas legislativas",
        "Riesgo de desajustes fiscales por reformas",
        "Falta de capacidad de generar ingresos fiscales", "Riesgo de gasto excesivo",
        "Incremento del gasto público no controlado", "Medidas de ajuste fiscal",
        "Inestabilidad presupuestaria", "Riesgo de inestabilidad fiscal",
        "Falta de sostenibilidad de la deuda", "Compromiso con la disciplina fiscal",
        "Necesidad de mejorar la disciplina fiscal", "Riesgos derivados de la crisis financiera",
        "Emergencia fiscal", "No cumplimiento de los límites de deuda",
        "Riesgo de presión sobre las finanzas públicas", "Riesgos de sostenibilidad a largo plazo",
        "Inconsistencia en las proyecciones fiscales", "Proyecciones fiscales no realistas",
        "Implicaciones fiscales de la situación de Petroperú",
        "Desajuste en las proyecciones fiscales", "Necesidad de consolidación fiscal",
        "Riesgos de desequilibrio fiscal", "Amenaza a la estabilidad fiscal",
        "Inseguridad fiscal", "Inconsistencias fiscales", "Falta de previsión en el gasto",
        "Riesgo de pérdida de control fiscal", "Impacto fiscal no anticipado",
        "Presión de gastos adicionales", "Aumento en la presión fiscal",
        "Erosión de las finanzas públicas", "Riesgo de déficit fiscal no controlado",
        "Aumento de la carga fiscal", "Riesgo de crisis fiscal",
        "Propuestas legislativas que generan gasto",
        "Propuestas que limitan la recaudación fiscal",
        "Iniciativas fiscales con implicaciones negativas",
        "Aumento de los gastos sociales no previstos",
        "Riesgo de incumplimiento de los límites fiscales",
        "Propuestas legislativas que no cumplen con las reglas fiscales",
        "Desviaciones fiscales no justificadas",
        "Proyecciones de déficit fiscal no alcanzables",
        "Riesgos derivados de iniciativas legislativas excesivas",
        "Crecimiento de la deuda pública sin control",
        "Necesidad de políticas fiscales más estrictas"
    ]

    # Convertimos a minúsculas para búsqueda robusta
    keywords_lower = [k.lower() for k in keywords]
    df_result = df_result[
        df_result["text"].str.lower().apply(
            lambda txt: any(k in txt for k in keywords_lower)
        )
    ].reset_index(drop=True)

In [ ]:
with pdfplumber.open(r"C:\Users\Jason Cruz\OneDrive\Documentos\RA\CIUP\Policy Brief\CF\opiniones\Comunicado-01-2025-ReglasFiscales-vf-1.pdf") as pdf:
    for word in pdf.pages[0].extract_words(extra_attrs=["size"]):
        print(f"'{word['text']}' → size: {word['size']}")


In [ ]:
df_cleaned = clean_noise(df_parrafos)

In [ ]:
df_cleaned

In [ ]:
print(len(df_cleaned))

In [20]:
df_parrafos_cleaned[df_parrafos_cleaned["text"].str.match(r"^[a-záéíóúñ]")]

filename  year  \
125   CF-Informe-MMM2124-cNotaAclaratoria-28-de-agosto-VF-publicada.pdf  2020   
593                                               InformeCF-IAPM-VF.pdf  2019   
595                                               InformeCF-IAPM-VF.pdf  2019   
641                           Opinion-MMM2023-2026-cNotaAclaratoria.pdf  2026   
690                  Pronunciamiento-CF-DCRF-2017-12julio-enviada-1.pdf  2018   
691                  Pronunciamiento-CF-DCRF-2017-12julio-enviada-1.pdf  2018   
788                         Pronunciamiento-FinanzasPublicas2022-vF.pdf  2023   
899                                    Pronunciamiento-IAPM24-27-vf.pdf  2024   
1137                                  Pronunciamiento-pMMM-25-28-vf.pdf  2024   
1224               Pronunciamiento-suspension-de-reglas-fiscales-VF.pdf  None   

                      date announcement  page  paragraph_id  \
125   14 de agosto de 2020         None    16            86   
593     21 de mayo de 2019         None     7            31   
595     21 de mayo de 2019         None     7            33   
641                   None           23    10            34   
690    12 de julio de 2018         None     4            17   
691    12 de julio de 2018         None     5            18   
788    30 de junio de 2023         None     3            12   
899     16 de mayo de 2024         None     2             4   
1137  15 de agosto de 2024         None     4            14   
1224                  None         None     4            18   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          text  
125   permanente de recaudación sustentada a partir de la efectividad y maduración de un conjunto de medidas tributarias implementadas desde el 2017, determinan un sesgo optimista en la proyección de ingresos públicos de mediano plazo. Además, el CF nota que el gasto no financiero promedio móvil para dicho periodo previsto en el MMM, de 21,1 por ciento del del PBI, es el nivel más alto desde fines de los años setenta, lo cual no es consistente con la necesidad de reconstruir las cuentas fiscales del país, retomar la senda de sostenibilidad de la deuda pública e iniciar un proceso de consolidación fiscal. En este contexto, el mayor riesgo fiscal estará determinado por la poca capacidad para generar mayores ingresos permanentes, frente a la rigidez y el nivel de gasto planteado para el mediano plazo. En consecuencia, el CF considera que se debe adoptar una senda de consolidación creíble en el mediano plazo y definir un límite de deuda pública, a la luz de la nueva situación macroeconómica, para establecer dicha convergencia.  
593                                                                                                                                                                                                                                                                                                                                   lugar del 20,5 por ciento del PBI previsto para ese año. Para poder c

In [21]:
print(len(df_parrafos_cleaned))

1305


In [ ]:
import pandas as pd

# Filtrar las filas donde el texto en la columna 'text' contiene expresiones específicas
df_3 = df_cleaned[~df_cleaned['text'].str.endswith('.', na=False)]

In [ ]:
df_3

In [ ]:
print(len(df_3))

In [ ]:
df_cleaned[df_cleaned["date"]=="16 de setiembre de 2020"]

# Scanned

In [ ]:
df_scanned_cleaned = clean_noise(df_scanned)

In [ ]:
df_scanned_cleaned

In [ ]:
print(len(df_scanned_cleaned))

In [ ]:
import pandas as pd

# Filtrar las filas donde el texto en la columna 'text' contiene expresiones específicas
df_4 = df_scanned_cleaned[df_scanned_cleaned['text'].str.contains(r"^%", na=False)]

In [ ]:
df_4

In [ ]:
print(len(df_4))

# Eliminar outliers

## Agregar columna de "lenght" para saber cuántos caracteres (sin espacio) tiene cada parrafo

In [ ]:
# Calcular el número de caracteres en cada texto
df_cleaned['text_length'] = df_cleaned['text'].str.len()

In [ ]:
# Calcular estadísticas descriptivas
min_length = df_cleaned['text_length'].min()
max_length = df_cleaned['text_length'].max()
mean_length = df_cleaned['text_length'].mean()
median_length = df_cleaned['text_length'].median()
percentile_5 = df_cleaned['text_length'].quantile(0.05)
percentile_75 = df_cleaned['text_length'].quantile(0.75)
iqr = percentile_75 - percentile_5

In [ ]:
percentile_5

In [ ]:
median_length

In [ ]:
iqr

In [ ]:
# Calcular los límites inferior y superior para los outliers
lower_bound = percentile_5
upper_bound = percentile_75

# Filtrar los textos que están dentro del rango de tamaño de texto aceptable
df_filtered = df_cleaned[(df_cleaned['text_length'] >= lower_bound) & (df_cleaned['text_length'] <= upper_bound)]

# Mostrar los resultados de las estadísticas
print(f"Min: {min_length}")
print(f"Max: {max_length}")
print(f"Mean: {mean_length}")
print(f"Median: {median_length}")
print(f"25th Percentile: {percentile_5}")
print(f"75th Percentile: {percentile_75}")
print(f"IQR: {iqr}")
print(f"Lower Bound (Outliers below): {lower_bound}")
print(f"Upper Bound (Outliers above): {upper_bound}")

In [ ]:
df_filtered

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

<div id="2"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h1 style="text-align: left; color: #E0E0E0;">
        2. Sentiment analysis by zero-shot
    </h1>
</div>

<div id="2-1"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #ff8575;">
        2.1 Define the model (<code>xlm-roberta-base</code>)
    </h2>
</div>

In [ ]:
from transformers import pipeline
import pandas as pd

# Cargar el pipeline de clasificación zero-shot
classifier = pipeline("zero-shot-classification", model="facebook/bart-large-mnli")


In [ ]:
# model="facebook/bart-large-mnli"
# model="distilbert-base-multilingual-cased"
# model="bert-base-spanish-wwm-uncased"
# model="xlm-roberta-base"
# model="bert-base-multilingual-cased"
# model="roberta-base" # similar than xlm-roberta-base

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

<div id="2-2"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #ff8575;">
        2.2 Define the labels
    </h2>
</div>

In [ ]:
candidate_labels = ["Disciplina Fiscal Exitosa", "Advertencia Fiscal", "Incumplimiento Fiscal Grave", "Riesgo Fiscal Inminente"]

<div id="2-3"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #ff8575;">
        2.3 Applying the model to the paragraphs
    </h2>
</div>

In [ ]:
def classify_sentiment(text):
    return classifier(text, candidate_labels)

In [ ]:
df_cleaned['sentiment'] = df_cleaned['text'].apply(lambda x: classify_sentiment(x))

In [ ]:
df_cleaned

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

<div id="2-4"; style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #ff8575;">
        2.4 Sentiment aggregation by announcement
    </h2>
</div>

In [ ]:
def aggregate_sentiment(df):
    aggregated_sentiment = []

    # Loop through each file (grouping by filename)
    for filename, group in df.groupby('filename'):
        # Extract the metadata columns for this file (same for all paragraphs)
        year = group['year'].iloc[0]
        date = group['date'].iloc[0]
        announcement = group['announcement'].iloc[0]
        
        # Initialize an empty list to store the sentiment scores for each label
        all_scores = {label: [] for label in candidate_labels}

        # Loop through each paragraph to gather the scores
        for _, row in group.iterrows():
            sentiment = row['sentiment']
            # Loop through the labels and their scores
            for label, score in zip(sentiment['labels'], sentiment['scores']):
                all_scores[label].append(score)

        # Calculate the mean score for each label (across all paragraphs in the file)
        mean_scores = {label: sum(scores) / len(scores) for label, scores in all_scores.items()}

        # Append the result for this file, including metadata columns and sentiment scores
        aggregated_sentiment.append({
            'filename': filename,
            'year': year,
            'date': date,
            'announcement': announcement,
            **mean_scores  # Include average scores for each label
        })

    return pd.DataFrame(aggregated_sentiment)


In [ ]:
aggregated_sentiment_df = aggregate_sentiment(df_cleaned)
aggregated_sentiment_df

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: #033280; font-weight: bold;">
        <a href="#outilne" style="color: #033280; text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: #cd301b; text-decoration: none;">Back to the outline.</a>
</div>

In [ ]:
aggregated_sentiment_df["date"]

In [ ]:
# Save the modified dataframe to a new variable
modified_sentiment_df = aggregated_sentiment_df.copy()

In [ ]:
# Create a dictionary to map Spanish months to English ones
month_translation = {
    'enero': 'January',
    'febrero': 'February',
    'marzo': 'March',
    'abril': 'April',
    'mayo': 'May',
    'junio': 'June',
    'julio': 'July',
    'agosto': 'August',
    'septiembre': 'September',
    'octubre': 'October',
    'noviembre': 'November',
    'diciembre': 'December'
}

# Function to convert Spanish date format to standard datetime
def parse_spanish_date(date_str):
    for month_spanish, month_english in month_translation.items():
        if month_spanish in date_str:
            # Replace Spanish month with English month and remove 'de'
            date_str = date_str.replace(month_spanish, month_english).replace(' de ', ' ')
            break
    # Clean up any extra spaces around the date
    date_str = date_str.strip()
    try:
        # Try to convert to datetime with inferred format
        return pd.to_datetime(date_str, errors='coerce')
    except Exception as e:
        # If there's an issue, return NaT
        print(f"Error parsing date: {date_str} - {e}")
        return pd.NaT

In [ ]:
# Apply the function to the 'date' column
modified_sentiment_df['date'] = modified_sentiment_df['date'].apply(parse_spanish_date)


In [ ]:
modified_sentiment_df

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns

# Ensure the 'date' column is in datetime format
modified_sentiment_df['date'] = pd.to_datetime(modified_sentiment_df['date'])

# Sort the dataframe by date
modified_sentiment_df = modified_sentiment_df.sort_values(by="date")

# Melt the dataframe so that each row corresponds to one date and one value
df_melted = modified_sentiment_df.melt(id_vars=["date"], 
                                       value_vars=["Disciplina Fiscal Exitosa", 
                                                   "Advertencia Fiscal", 
                                                   "Incumplimiento Fiscal Grave", 
                                                   "Riesgo Fiscal Inminente"],
                                       var_name="Fiscal Indicator", 
                                       value_name="Value")

# Create the plot
plt.figure(figsize=(10, 6))

# Use seaborn barplot to plot the data
sns.barplot(x="date", y="Value", hue="Fiscal Indicator", data=df_melted)

# Rotate x labels for better readability
plt.xticks(rotation=45, ha='right')

# Add titles and labels
plt.title('Fiscal Indicators by Date')
plt.xlabel('Date')
plt.ylabel('Value')

# Show the plot
plt.tight_layout()
plt.show()


# Agenda

* Apply the same as above to the CF reports
* Test sentiment analysis using Fine-tuned and LLM
* Create a so-called “Fiscal Tone Index”.
* Explore correlations
* Visualize the data

### Brainstorming on "Fiscal Tone Index"

1. Assignment of numerical values to the sentiment labels.

In [ ]:
# Asignar un valor numérico a cada etiqueta de sentimiento
#sentiment_values = {
#    "Disciplina Fiscal Exitosa": 1,
#    "Advertencia Fiscal": 0,
#    "Incumplimiento Fiscal Grave": -1,
#    "Riesgo Fiscal Inminente": -2
#}

# Función para obtener el valor numérico de la etiqueta de sentimiento
#def get_sentiment_value(sentiment_label):
#    return sentiment_values.get(sentiment_label, 0)  # Devuelve 0 si no se encuentra la etiqueta


2. Modification of the analysis to add the numerical value of each sentiment:

In [ ]:
#def aggregate_sentiment_with_values(df):
#    aggregated_sentiment = []
#    
#    for filename, group in df.groupby('filename'):
#        # Obtener la etiqueta de sentimiento más frecuente
#        sentiments = group['sentiment'].apply(lambda x: x['labels'][x['scores'].index(max(x['scores']))])
#        
#        # Obtener los valores numéricos de las etiquetas de sentimiento
#        sentiment_values_list = [get_sentiment_value(sentiment) for sentiment in sentiments]
#        
#        # Calcular el índice de tono fiscal como la media de los valores numéricos
#        fiscal_tone_index = sum(sentiment_values_list) / len(sentiment_values_list) if sentiment_values_list else 0
#        
#        aggregated_sentiment.append({
#            'filename': filename,
#            'fiscal_tone_index': fiscal_tone_index  # Agregar el índice de tono fiscal
#        })
#    
#    return pd.DataFrame(aggregated_sentiment)


Finally, it calls the <code>aggregate_sentiment_with_values</code> function to calculate the fiscal tone index for each release.

In [ ]:
#aggregated_sentiment_df = aggregate_sentiment_with_values(df_cleaned)
#aggregated_sentiment_df

* Assignment of numeric values: We assign a numeric value to each sentiment label with the sentiment_values dictionary. This value reflects the “severity” of the sentiment (positive or negative).

* Calculation of the fiscal tone index: For each release (grouped by filename), we calculate the average of the numeric sentiment values of the paragraphs within that release. The fiscal tone index is calculated by summing the numeric values of all paragraphs and dividing by the number of paragraphs.

* Normalization (optional): If you want the index to be in a range from 0 to 100 or between -1 and 1, you can apply a normalization. For example, if you want the values to be between -1 and 1, you can use a formula like this:

In [ ]:
# normalized_index = (fiscal_tone_index - min_value) / (max_value - min_value) * 2 - 1